In [1]:
#Import Libraries
from selenium import webdriver
from selenium.webdriver.support.ui import Select
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.common.exceptions import NoSuchElementException,TimeoutException
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import StaleElementReferenceException
import pandas as pd
import lxml
import os
import time
import datetime
import json

In [2]:
#Start Timmer
start = time.time()

#Set Output Folder
output_folder = datetime.datetime.now().strftime("Date-%Y-%m-%d-Time-%H-%M-%S")
if not os.path.exists(output_folder):
    os.makedirs(output_folder)

In [3]:
#Start Chrome
driver = webdriver.Chrome()
driver.implicitly_wait(20) # seconds

#Prepare URL
protocol = "https://"
url = protocol + "rhreporting.nic.in/netiay/PhysicalProgressReport/YearWiseHouseCompletionReport.aspx?"
params = {
    'params': 0
}
for key, value in params.items():
    url = url + "&" + key + "=" + str(value)

#Playing with headers
my_referer = url
UserAgent = 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_10_1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/39.0.2171.95 Safari/537.36'
mod_headers = {'referer': my_referer, 'User-Agent':UserAgent}

#Start Chrome
driver.get(url)

In [4]:
# Select List
year_select_name = 'ctl00$ContentPlaceHolder1$ddlFinYear'
scheme_select_name = 'ctl00$ContentPlaceHolder1$ddlScheme'
state_select_name = 'ctl00$ContentPlaceHolder1$ddlState'
district_select_name = 'ctl00$ContentPlaceHolder1$ddlDistrict'
block_select_name = 'ctl00$ContentPlaceHolder1$ddlBlock'
submit_button_name = 'ctl00$ContentPlaceHolder1$btnSubmit'
content_table_pane = 'ContentPlaceHolder1_gvDataPanelItem'
content_table_head_id = 'ContentPlaceHolder1_gvDataCopy'
content_table_id = 'ContentPlaceHolder1_gvData'

In [5]:
#Build State List
def build_list(element_name):
    temp_list = driver.find_element_by_name(element_name).find_elements_by_xpath(".//option")[1:]
    _list = []
    #loop over each option
    for x in temp_list:
        d = {}
        d['text'] = x.text
        d['value'] = x.get_attribute('value')
        _list.append(d)
        #print("_list index:",i,d)
    return _list

#Check Submit button
def delete_submit():
    driver.execute_script("return document.getElementsByName('" + submit_button_name + "')[0].remove()")
def check_submit():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.NAME, submit_button_name ) ) )

#Check table
def delete_submit():
    driver.execute_script("return document.getElementsByName('" + submit_button_name + "')[0].remove()")
def check_submit():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.NAME, submit_button_name ) ) )    
    
#Check submit button
def delete_content():
    driver.execute_script("return document.getElementsByClassName('col-lg-10')[0].remove()")
def check_error():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.ID, "ContentPlaceHolder1_lbl_data_msg" ) ) )
    

In [6]:
def get_total_houselist():
    #Wait for Table to Load fully
    element_present = EC.presence_of_element_located((By.ID, content_table_id))            
    WebDriverWait(driver, 2).until(element_present)
    #Once Loaded Create DataFrame from Table
    html_table = driver.find_element_by_id(content_table_id).get_attribute('outerHTML')
    df = pd.read_html(html_table, skiprows=0, header=0)[0]
    df = df[1:-1]        
    total_houses_completed = list(df[df.columns[-1]])
    return total_houses_completed

In [7]:
#Start Chrome
driver.get(url)

#Year Selection
element = WebDriverWait(driver, 10).until(
    EC.element_to_be_clickable((By.NAME, year_select_name))
)
element.find_element_by_xpath(".//option[@value='0']").click()
yearlist = build_list(year_select_name)[5:6]
for year in yearlist:    
    print("--Scrapping data for Year: ", year['text'])
    year_query = ".//option[@value='" + year['value'] + "']"
    delete_submit()
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, year_select_name))
    )
    element.find_element_by_xpath(year_query).click()
    check_submit()
    
    #DataStore
    df_list = []
    
    #Scheme Selection
    schemelist = build_list(scheme_select_name)[11:]
    for scheme in schemelist:
        print("--//--Scrapping data for scheme: ", scheme['text'])
        scheme_query = ".//option[@value='" + scheme['value'] + "']"
        delete_submit()
        element = WebDriverWait(driver, 10).until(
            EC.element_to_be_clickable((By.NAME, scheme_select_name))
        )
        element.find_element_by_xpath(scheme_query).click()
        check_submit()
        
        # Delete Content
        delete_content()        
        #Submit button
        element = WebDriverWait(driver, 10).until(
            EC.element_to_be_clickable((By.NAME, submit_button_name))
        )
        element.click()
        
        #Load Filter List
        state_total_houses_completed = get_total_houselist();
        
        #state Selection
        statelist = build_list(state_select_name)
        for stateindex, state in enumerate(statelist):
            print("--//--//--Scrapping data for state: ", state['text'])
            if state_total_houses_completed[int(stateindex)] > 0:
                state_query = ".//option[@value='" + state['value'] + "']"
                delete_submit()
                element = WebDriverWait(driver, 10).until(
                    EC.element_to_be_clickable((By.NAME, state_select_name))
                )
                element.find_element_by_xpath(state_query).click()
                check_submit()
                
                # Delete Content
                delete_content()        
                #Submit button
                element = WebDriverWait(driver, 10).until(
                    EC.element_to_be_clickable((By.NAME, submit_button_name))
                )
                element.click()

                #Load Filter List
                district_total_houses_completed = get_total_houselist();
         
                #district Selection
                districtlist = build_list(district_select_name)
                for districtindex, district in enumerate(districtlist):
                    print("--//--//--//--Scrapping data for district: ", district['text'])
                    if district_total_houses_completed[int(districtindex)] > 0:
                        district_query = ".//option[@value='" + district['value'] + "']"
                        delete_submit()
                        element = WebDriverWait(driver, 10).until(
                            EC.element_to_be_clickable((By.NAME, district_select_name))
                        )
                        element.find_element_by_xpath(district_query).click()
                        check_submit()
                        
                        # Delete Content
                        delete_content()        
                        #Submit button
                        element = WebDriverWait(driver, 10).until(
                            EC.element_to_be_clickable((By.NAME, submit_button_name))
                        )
                        element.click()

                        #Load Filter List
                        block_total_houses_completed = get_total_houselist();

                        #block Selection
                        blocklist = build_list(block_select_name)
                        for blockindex, block in enumerate(blocklist):
                            print("--//--//--//--//--Scrapping data for block: ", block['text'])
                            if block_total_houses_completed[int(blockindex)] > 0:
                                block_query = ".//option[@value='" + block['value'] + "']"
                                delete_submit()
                                element = WebDriverWait(driver, 10).until(
                                    EC.element_to_be_clickable((By.NAME, block_select_name))
                                )
                                element.find_element_by_xpath(block_query).click()
                                check_submit()

                                # Delete Content
                                delete_content()

                                #Submit button
                                element = WebDriverWait(driver, 10).until(
                                    EC.element_to_be_clickable((By.NAME, submit_button_name))
                                )
                                element.click()

                                try:
                                    #Wait for Table to Load fully
                                    element_present = EC.presence_of_element_located((By.ID, content_table_id))            
                                    WebDriverWait(driver, 2).until(element_present)

                                    #Once Loaded Create DataFrame from Table
                                    #html_head = driver.find_element_by_id(content_table_head_id).get_attribute('outerHTML')
                                    #df = pd.read_html(html_head, skiprows=0)[0]
                                    #table_head = list(df.values[0])
                                    html_table = driver.find_element_by_id(content_table_id).get_attribute('outerHTML')
                                    df = pd.read_html(html_table, skiprows=0, header=0)[0]
                                    df = df[1:-1]
                                    #df.columns = table_head
                                    df['Financial Year'] = year['text']
                                    df['Scheme'] = scheme['text']
                                    df['State Name'] = state['text']
                                    df['District Name'] = district['text']
                                    df['Block Name'] = block['text']
                                    df_list.append(df)
                                except Exception as e:
                                    print("Error while table data |", e)


    #merge all dataframes to master dataframe
    df = pd.concat(df_list)
    df = df.reset_index().drop(columns=['index', '#SNo'])
    df['#SNo'] = df.index + 1
    #Save Scrapped File
    df.to_csv(os.path.join(output_folder, year['text']+'_Scrapped_Data.csv'), encoding='utf-8', index=False)

--Scrapping data for Year:  2015-2016
--//--Scrapping data for scheme:  CYCLONE PHAILIN
--//--//--Scrapping data for state:  ARUNACHAL PRADESH
--//--//--Scrapping data for state:  ASSAM
--//--//--Scrapping data for state:  BIHAR
--//--//--Scrapping data for state:  CHHATTISGARH
--//--//--Scrapping data for state:  GOA
--//--//--Scrapping data for state:  GUJARAT
--//--//--Scrapping data for state:  HARYANA
--//--//--Scrapping data for state:  HIMACHAL PRADESH
--//--//--Scrapping data for state:  JAMMU AND KASHMIR
--//--//--Scrapping data for state:  JHARKHAND
--//--//--Scrapping data for state:  KERALA
--//--//--Scrapping data for state:  MADHYA PRADESH
--//--//--Scrapping data for state:  MAHARASHTRA
--//--//--Scrapping data for state:  MANIPUR
--//--//--Scrapping data for state:  MEGHALAYA
--//--//--Scrapping data for state:  MIZORAM
--//--//--Scrapping data for state:  NAGALAND
--//--//--Scrapping data for state:  ODISHA
--//--//--//--Scrapping data for district:  ANGUL
--//--//--//

--//--//--//--Scrapping data for district:  KORAPUT
--//--//--//--Scrapping data for district:  MALKANGIRI
--//--//--//--Scrapping data for district:  MAYURBHANJ
--//--//--//--Scrapping data for district:  NABARANGAPUR
--//--//--//--Scrapping data for district:  NAYAGARH
--//--//--//--//--Scrapping data for block:  BHAPUR
--//--//--//--//--Scrapping data for block:  DASAPALLA
--//--//--//--//--Scrapping data for block:  GANIA
--//--//--//--//--Scrapping data for block:  KHANDAPARA
--//--//--//--//--Scrapping data for block:  NAYAGARH
--//--//--//--//--Scrapping data for block:  NUAGAON
--//--//--//--//--Scrapping data for block:  ODAGAON
--//--//--//--//--Scrapping data for block:  RANAPUR
--//--//--//--Scrapping data for district:  NUAPADA
--//--//--//--Scrapping data for district:  PURI
--//--//--//--//--Scrapping data for block:  ASTARANGA
--//--//--//--//--Scrapping data for block:  BRAHMAGIRI
--//--//--//--//--Scrapping data for block:  DELANGA
--//--//--//--//--Scrapping data for

--//--//--//--//--Scrapping data for block:  DIDIHAT
--//--//--//--//--Scrapping data for block:  GANGOLIHAT
--//--//--//--//--Scrapping data for block:  KANALICHINA
--//--//--//--//--Scrapping data for block:  MUNAKOT
--//--//--//--//--Scrapping data for block:  MUNSYARI
--//--//--//--//--Scrapping data for block:  PITHORAGARH
--//--//--//--Scrapping data for district:  RUDRA PRAYAG
--//--//--//--//--Scrapping data for block:  AUGUSTYAMUNI
--//--//--//--//--Scrapping data for block:  JAKHOLI
--//--//--//--//--Scrapping data for block:  UKHIMATH
--//--//--//--Scrapping data for district:  TEHRI GARHWAL
--//--//--//--Scrapping data for district:  UDAM SINGH NAGAR
--//--//--//--Scrapping data for district:  UTTAR KASHI
--//--//--//--//--Scrapping data for block:  BHATWARI
--//--//--//--//--Scrapping data for block:  CHINYALISAUR
--//--//--//--//--Scrapping data for block:  DUNDA
--//--//--//--//--Scrapping data for block:  MORI
--//--//--//--//--Scrapping data for block:  NAUGAON
--//--/

--//--//--//--Scrapping data for district:  AGAR-MALWA
--//--//--//--Scrapping data for district:  ALIRAJPUR
--//--//--//--Scrapping data for district:  ANUPPUR
--//--//--//--Scrapping data for district:  ASHOK NAGAR
--//--//--//--Scrapping data for district:  BALAGHAT
--//--//--//--Scrapping data for district:  BARWANI
--//--//--//--Scrapping data for district:  BETUL
--//--//--//--//--Scrapping data for block:  AMLA
--//--//--//--//--Scrapping data for block:  ATHNER
--//--//--//--//--Scrapping data for block:  BETUL
--//--//--//--//--Scrapping data for block:  BHAINSDEHI
--//--//--//--//--Scrapping data for block:  BHIMPUR
--//--//--//--//--Scrapping data for block:  CHICHOLI
--//--//--//--//--Scrapping data for block:  GHORA DONGRI
--//--//--//--//--Scrapping data for block:  MULTAI
--//--//--//--//--Scrapping data for block:  PRABHAT PATTAN
--//--//--//--//--Scrapping data for block:  SHAHPUR
--//--//--//--Scrapping data for district:  BHIND
--//--//--//--Scrapping data for distri

--//--//--//--Scrapping data for district:  JHARSUGUDA
--//--//--//--Scrapping data for district:  KALAHANDI
--//--//--//--Scrapping data for district:  KANDHAMAL
--//--//--//--//--Scrapping data for block:  BALIGUDA
--//--//--//--//--Scrapping data for block:  CHAKAPAD
--//--//--//--//--Scrapping data for block:  DARINGIBADI
--//--//--//--//--Scrapping data for block:  G.UDAYAGIRI
--//--//--//--//--Scrapping data for block:  K.NUAGAN
--//--//--//--//--Scrapping data for block:  KHAJURIPADA
--//--//--//--//--Scrapping data for block:  KOTAGARH
--//--//--//--//--Scrapping data for block:  PHIRINGIA
--//--//--//--//--Scrapping data for block:  PHULBANI
--//--//--//--//--Scrapping data for block:  RAIKIA
--//--//--//--//--Scrapping data for block:  TIKABALI
--//--//--//--//--Scrapping data for block:  TUMUDIBANDH
--//--//--//--Scrapping data for district:  KENDRAPARA
--//--//--//--Scrapping data for district:  KENDUJHAR
--//--//--//--//--Scrapping data for block:  ANANDAPUR
--//--//--//--

...

--//--//--//--//--Scrapping data for block:  RAJOUND
--//--//--//--//--Scrapping data for block:  SIWAN
--//--//--//--Scrapping data for district:  KARNAL
--//--//--//--//--Scrapping data for block:  ASSANDH
--//--//--//--//--Scrapping data for block:  GHARAUNDA (PART)
--//--//--//--//--Scrapping data for block:  INDRI
--//--//--//--//--Scrapping data for block:  KARNAL
--//--//--//--//--Scrapping data for block:  NILOKHERI
--//--//--//--//--Scrapping data for block:  NISSING AT CHIRAO
--//--//--//--Scrapping data for district:  KURUKSHETRA
--//--//--//--//--Scrapping data for block:  BABAIN
--//--//--//--//--Scrapping data for block:  ISMAILABAD
--//--//--//--//--Scrapping data for block:  LADWA
--//--//--//--//--Scrapping data for block:  PEHOWA
--//--//--//--//--Scrapping data for block:  SHAHBAD
--//--//--//--//--Scrapping data for block:  THANESAR
--//--//--//--Scrapping data for district:  MAHENDRAGARH
--//--//--//--//--Scrapping data for block:  ATELI NANGAL
--//--//--//--//--Sc

--//--//--//--//--Scrapping data for block:  BALH
--//--//--//--//--Scrapping data for block:  CHAUNTRA
--//--//--//--//--Scrapping data for block:  DHARAMPUR
--//--//--//--//--Scrapping data for block:  DRANG
--//--//--//--//--Scrapping data for block:  GOHAR
--//--//--//--//--Scrapping data for block:  GOPALPUR
--//--//--//--//--Scrapping data for block:  KARSOG
--//--//--//--//--Scrapping data for block:  MANDI SADAR
--//--//--//--//--Scrapping data for block:  SERAJ
--//--//--//--//--Scrapping data for block:  SUNDERNAGAR
--//--//--//--Scrapping data for district:  SHIMLA
--//--//--//--//--Scrapping data for block:  BASANTPUR
--//--//--//--//--Scrapping data for block:  CHAUHARA
--//--//--//--//--Scrapping data for block:  CHOPAL
--//--//--//--//--Scrapping data for block:  JUBBAL KOTKHAI
--//--//--//--//--Scrapping data for block:  MASHOBRA
--//--//--//--//--Scrapping data for block:  NANKHARI
--//--//--//--//--Scrapping data for block:  NARKANDA
--//--//--//--//--Scrapping data f

--//--//--Scrapping data for state:  ARUNACHAL PRADESH
--//--//--Scrapping data for state:  ASSAM
--//--//--Scrapping data for state:  BIHAR
--//--//--Scrapping data for state:  CHHATTISGARH
--//--//--Scrapping data for state:  GOA
--//--//--Scrapping data for state:  GUJARAT
--//--//--Scrapping data for state:  HARYANA
--//--//--Scrapping data for state:  HIMACHAL PRADESH
--//--//--Scrapping data for state:  JAMMU AND KASHMIR
--//--//--Scrapping data for state:  JHARKHAND
--//--//--Scrapping data for state:  KERALA
--//--//--Scrapping data for state:  MADHYA PRADESH
--//--//--Scrapping data for state:  MAHARASHTRA
--//--//--Scrapping data for state:  MANIPUR
--//--//--Scrapping data for state:  MEGHALAYA
--//--//--Scrapping data for state:  MIZORAM
--//--//--Scrapping data for state:  NAGALAND
--//--//--Scrapping data for state:  ODISHA
--//--//--Scrapping data for state:  PUNJAB
--//--//--Scrapping data for state:  RAJASTHAN
--//--//--Scrapping data for state:  SIKKIM
--//--//--Scrap

--//--//--//--Scrapping data for district:  PURNIA
--//--//--//--Scrapping data for district:  ROHTAS
--//--//--//--Scrapping data for district:  SAHARSA
--//--//--//--Scrapping data for district:  SAMASTIPUR
--//--//--//--Scrapping data for district:  SARAN
--//--//--//--Scrapping data for district:  SHEIKHPURA 
--//--//--//--Scrapping data for district:  SHEOHAR
--//--//--//--Scrapping data for district:  SITAMARHI
--//--//--//--Scrapping data for district:  SIWAN
--//--//--//--Scrapping data for district:  SUPAUL
--//--//--//--Scrapping data for district:  VAISHALI
--//--//--//--//--Scrapping data for block:  BAGHWANPUR
--//--//--//--//--Scrapping data for block:  BIDUPUR
--//--//--//--//--Scrapping data for block:  CHEHRAKALA
--//--//--//--//--Scrapping data for block:  DESRI
--//--//--//--//--Scrapping data for block:  GAROUL
--//--//--//--//--Scrapping data for block:  HAJIPUR
--//--//--//--//--Scrapping data for block:  JANDAHA
--//--//--//--//--Scrapping data for block:  LALGAN

--//--//--Scrapping data for state:  ARUNACHAL PRADESH
--//--//--Scrapping data for state:  ASSAM
--//--//--Scrapping data for state:  BIHAR
--//--//--Scrapping data for state:  CHHATTISGARH
--//--//--Scrapping data for state:  GOA
--//--//--Scrapping data for state:  GUJARAT
--//--//--Scrapping data for state:  HARYANA
--//--//--Scrapping data for state:  HIMACHAL PRADESH
--//--//--Scrapping data for state:  JAMMU AND KASHMIR
--//--//--Scrapping data for state:  JHARKHAND
--//--//--Scrapping data for state:  KERALA
--//--//--Scrapping data for state:  MADHYA PRADESH
--//--//--Scrapping data for state:  MAHARASHTRA
--//--//--Scrapping data for state:  MANIPUR
--//--//--Scrapping data for state:  MEGHALAYA
--//--//--Scrapping data for state:  MIZORAM
--//--//--Scrapping data for state:  NAGALAND
--//--//--Scrapping data for state:  ODISHA
--//--//--//--Scrapping data for district:  ANGUL
--//--//--//--Scrapping data for district:  BALESHWAR
--//--//--//--//--Scrapping data for block:  B

In [10]:
df = pd.concat(df_list)

In [11]:
df

#SNo   Panchayat Name  Houses completed for prior to 2010-2011  \
1    1.0          CHANGBU                                        0   
2    2.0       CHANGPRONG                                        0   
3    3.0        LEBRAJANG                                        0   
4    4.0       LEMBERDUNG                                        0   
5    5.0       SERU MEITH                                        0   
6    6.0        SERU TOTH                                        0   
7    7.0       SHYO MEITH                                        0   
8    8.0        SHYO TOTH                                        0   
9    9.0            SURBI                                        0   
10  10.0         TSAIGHAR                                        0   
1    1.0           Barama                                        0   
2    2.0        Debachara                                        0   
3    3.0        Kaklabari                                        0   
4    4.0        Kharuajan                                        0   
5    5.0         Merkuchi                                        0   
6    6.0      Puransripur                                        0   
1    1.0             Adla                                        0   
2    2.0       Angardhowa                                        0   
3    3.0        Baganpara                                        0   
4    4.0       Bagulamari                                        0   
5    5.0            Gerua                                        0   
6    6.0        Ghoramara                                        0   
7    7.0         Jopadong                                        0   
8    8.0        Pakhamara                                        0   
9    9.0       Subankhata                                        0   
1    1.0       Gandhibari                                        0   
2    2.0         Kaurbaha                                        0   
3    3.0       Khatarbari                                        0   
4    4.0         Mazagari                                        0   
5    5.0        Nagrijuli                                        0   
..   ...              ...                                      ...   
17  17.0           RALABA                                        0   
18  18.0          SAHAPUR                                        0   
19  19.0             SARU                                        0   
20  20.0     SASANAMBAGAM                                        0   
21  21.0           SIKIRI                                        0   
1    1.0         ADHEIGAM                                        0   
2    2.0            ALADI                                        0   
3    3.0       ALLASUGUMA                                        0   
4    4.0          B.D.PUR                                        0   
5    5.0          BARAGAM                                        0   
6    6.0        BUDURUNGU                                        0   
7    7.0    CHADHEIAPALLI                                        0   
8    8.0         CHAMUNDA                                        0   
9    9.0        GANDADHAR                                        0   
10  10.0        GAYAGANDA                                        0   
11  11.0           GERADA                                        0   
12  12.0  JAGANNATHPRASAD                                        0   
13  13.0       JHADABHUMI                                        0   
14  14.0         Jirabadi                                        0   
15  15.0            KADUA                                        0   
16  16.0     KHAMARAPALLI                                        0   
17  17.0     KHETAMUNDALI                                        0   
18  18.0         KOKALABA                                        0   
19  19.0          KUDUTAI                                        0   
20  20.0        KUMPAPADA                                        0   
21  21.0      

In [12]:
#merge all dataframes to master dataframe
df = pd.concat(df_list)
df = df.reset_index().drop(columns=['index', '#SNo'])
df['#SNo'] = df.index + 1
#Save Scrapped File
df.to_csv(os.path.join(output_folder, year['text']+'_Scrapped_Data.csv'), encoding='utf-8', index=False)